In [ ]:

from numpy import *
set_printoptions(legacy = "1.25")

def f(x): return sin(x)
def g(r): return 1/(1+ exp(-r))
def h(s): return s**2
# this for next example
def k(t): return cos(t)

func_chain = [f,g,h]

def df(x): return cos(x)
def dg(r): return g(r)*(1-g(r))
def dh(s): return 2*s
# this for next example
def dk(t): return -sin(t)

der_chain = [df,dg,dh]


In [ ]:


# first version: chains

def forward_prop(x_in,func_chain):
	x = [x_in]
	while func_chain:
		f = func_chain.pop(0)  # first func
		x_out = f(x_in)
		x.append(x_out) # insert at end
		x_in = x_out
	return x

from numpy import *
x_in = pi/4
x = forward_prop(x_in,func_chain)
x


In [ ]:

# dy/dy = 1
delta_out = 1


In [ ]:


# first version: chains

def backward_prop(delta_out,x,der_chain):
	delta = [delta_out]
	while der_chain:
		# discard last output
		x.pop(-1)
		df = der_chain.pop(-1) # last der
		der = df(x[-1])
		# chain rule -- multiply by previous der
		der = der * delta[0]
		delta.insert(0,der) # insert at start
	return delta
	
delta = backward_prop(delta_out,x,der_chain) 
delta


In [ ]:


d = 3
func_chain, der_chain = [h]*d, [dh]*d
x_in, delta_out = 5, 1

x = forward_prop(x_in,func_chain)
delta = backward_prop(delta_out,x,der_chain) 
x, delta


In [ ]:

d = 7
w = [ [None]*d for _ in range(d) ]

w[3][0] = w[3][1] = w[4][1] = w[4][2] = 1
w[5][3] = w[5][4] = w[6][5] = 1


In [ ]:

x0minus =  [None,None,None,None,None,None,None]
x1minus =  [None,None,None,None,None,None,None]
x2minus =  [None,None,None,None,None,None,None]
x3minus =  ['x','y',None,None,None,None,None]
x4minus =  [None,'y','z',None,None,None,None]
x5minus =  [None,None,None,'a','b',None,None]
x6minus =  [None,None,None,None,None,None,'J']


In [ ]:

x0minus =  [ ]
x1minus =  [ ]
x2minus =  [ ]
x3minus =  ['x','y']
x4minus =  ['y','z']
x5minus =  ['a','b']
x6minus =  ['J']


In [ ]:

activate = [None]*d

activate[3] = lambda x,y: x+y
activate[4] = lambda y,z: max(y,z)
activate[5] = lambda a,b: a*b


In [ ]:

def incoming(x,w,i):
	return [ w[i][j] * outgoing(x,w,j) for j in range(d) if w[i][j] ]


In [ ]:

def outgoing(x,w,i):
	if x[i] != None: return x[i]
	elif activate[i] != None: return activate[i](*incoming(x,w,i))
	else: return None


In [ ]:
  
# m = len(x_in)
# x[:m] = x_in


In [ ]:


# second version: networks

def forward_prop(x_in,w):
	d = len(w)
	x = [None]*d
	m = len(x_in)
	x[:m] = x_in
	for i in range(m,d): x[i] = outgoing(x,w,i)
	return x
	
x_in = [1,2,0]
x = forward_prop(x_in,w)
x


In [ ]:
  
# m = len(delta_out)
# delta[-m:] = delta_out


In [ ]:


g = [ [None]*d for _ in range(d) ]

# g specified only at neurons

g[3][0] = lambda x,y: 1
g[3][1] = lambda x,y: 1
g[4][1] = lambda y,z: 1 if y >= z else 0
g[4][2] = lambda y,z: 1 if z > y else 0
g[5][3] = lambda a,b: b
g[5][4] = lambda a,b: a


In [ ]:


def derivative(x,delta,g,j):
	if delta[j] != None: return delta[j]
	else:
		return sum([ derivative(x,delta,g,i) * g[i][j](*incoming(x,w,i)) * w[i][j] for i in range(d) if w[i][j] ])


In [ ]:


# second version: networks

def backward_prop(x,delta_out,g):
	d = len(g)
	delta = [None]*d
	m = len(delta_out)
	delta[-m:] = delta_out
	for j in range(d-m): delta[j] = derivative(x,delta,g,j)
	return delta

delta_out = [1,None]
delta = backward_prop(x,delta_out,g)
delta
